# RT Delay Analysis for ITP ID 290

In [1]:
import warnings
warnings.filterwarnings('ignore')

import os
os.environ["CALITP_BQ_MAX_BYTES"] = str(800_000_000_000)
import shared_utils
import utils

from siuba import *
import pandas as pd
import geopandas as gpd

import datetime as dt

import importlib
import rt_filter_map_plot

E0408 18:51:18.821997736    2772 fork_posix.cc:70]           Fork support is only compatible with the epoll1 and poll polling strategies


E0408 18:51:21.975731832    2772 fork_posix.cc:70]           Fork support is only compatible with the epoll1 and poll polling strategies


In [2]:
## parameters cell
itp_id = 290

In [3]:
# Parameters
itp_id = 290


In [4]:
analysis_date = dt.date(2022, 3, 30) ##TODO shift to Mar 30 for all?

In [5]:
trips = pd.read_parquet(f'{utils.GCS_FILE_PATH}rt_trips/{itp_id}_03_30.parquet')

In [6]:
stop_delay = gpd.read_parquet(f'{utils.GCS_FILE_PATH}stop_delay_views/{itp_id}_03_30.parquet')
stop_delay['arrival_time'] = stop_delay.arrival_time.map(lambda x: dt.datetime.fromisoformat(x))
stop_delay['actual_time'] = stop_delay.actual_time.map(lambda x: dt.datetime.fromisoformat(x))

In [7]:
%%capture
routelines = utils.get_routelines(itp_id, analysis_date)

In [8]:
%%capture
rt_day = rt_filter_map_plot.RtFilterMapper(trips, stop_delay, routelines)

In [9]:
%%capture
rt_day.set_filter(start_time='15:00', end_time='19:00')

In [10]:
%%capture
m = rt_day.segment_speed_map(how='low_speeds')

In [11]:
m

In [12]:
%%capture
rt_day.set_filter(start_time='07:00', end_time='09:00')

In [13]:
%%capture
m = rt_day.segment_speed_map(how='low_speeds')

In [14]:
m

In [15]:
metrics_df = (rt_day.rt_trips
     >> group_by(_.route_short_name, _.direction_id)
     >> summarize(speed_variance = _.mean_speed_mph.var(),
                 mean_speed_mph = _.mean_speed_mph.mean(),
                 min_hour = _.median_time.min().hour,
                 max_hour = _.median_time.max().hour)
     >> filter(_.min_hour <= 7, _.max_hour >= 15,
               _.mean_speed_mph < _.mean_speed_mph.quantile(.6),
               _.speed_variance)
     >> arrange(-_.speed_variance)
     >> head(20)
    )
metrics_df
## check that route has all-day span...

route_short_name direction_id  speed_variance  mean_speed_mph  min_hour  \
3                112            1       16.595013       12.476984         6   
42               280            1       12.002538       10.692380         6   
1                110            1       11.742926       12.011297         6   
28               250            1        8.253459       12.135994         6   
2                112            0        7.811515       15.339531         6   
121              ECR            1        6.969258       12.356663         1   
56               296            1        6.170729       12.404620         1   
55               296            0        5.788752       13.470587         3   
34               260            1        5.610045       14.281436         6   
120              ECR            0        5.539280       13.780200         4   
20                18            1        5.337013       14.409163         7   
6                121            0        5.255189       11.283565         6   
16               141            1        5.074021       10.928922         6   
44               281            1        5.029761       10.348170         7   
41               280            0        4.660548       12.090553         6   
5                120            1        4.005566       11.001325         4   
49               292            0        3.881122       13.249846         1   
10               130            0        3.769709       11.599489         5   
14               140            1        3.499200       14.867966         6   
43               281            0        3.485530       10.244518         6   

     max_hour  
3          21  
42         21  
1          22  
28         22  
2          20  
121        23  
56         23  
55         23  
34         18  
120        23  
20         16  
6          22  
16         19  
44         22  
41         21  
5          23  
49         23  
10         23  
14         22  
43         22

In [16]:
def map_from_metrics(rt_day, metrics_df):
    route_name = metrics_df.iloc[0,0]
    direction_id = metrics_df.iloc[0,1]
    # route_name = '281'
    # direction_id = '1'
    rt_day.set_filter(start_time='07:00', end_time='09:00',
                      route_names=[route_name], direction_id = direction_id)
    try:
        am_map = rt_day.segment_speed_map(how='low_speeds')
        display(am_map)
    except Exception as e:
        print(e)
        pass
    
    rt_day.set_filter(start_time='11:00', end_time='14:00',
                      route_names=[route_name], direction_id = direction_id)
    try:
        mid_map = rt_day.segment_speed_map(how='low_speeds')
        display(mid_map)
    except Exception as e:
        print(e)
        pass

    rt_day.set_filter(start_time='15:00', end_time='19:00',
                      route_names=[route_name], direction_id = direction_id)
    try:
        pm_map = rt_day.segment_speed_map(how='low_speeds')
        display(pm_map)
    except Exception as e:
        print(e)
        pass

    return

In [17]:
map_from_metrics(rt_day, metrics_df)

over 1% of geometries invalid after buffer+simplify


over 1% of geometries invalid after buffer+simplify


over 1% of geometries invalid after buffer+simplify
